<a href="https://colab.research.google.com/github/hadi-M/DS-Unit-2-Linear-Models/blob/master/module1-regression-1/HADI_MODARES_LS_DS_211_assignment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science

*Unit 2, Sprint 1, Module 1*

---

# Regression 1

## Assignment

You'll use another **New York City** real estate dataset. 

But now you'll **predict how much it costs to rent an apartment**, instead of how much it costs to buy a condo.

The data comes from renthop.com, an apartment listing website.

- [ ] Look at the data. Choose a feature, and plot its relationship with the target.
- [ ] Use scikit-learn for linear regression with one feature. You can follow the [5-step process from Jake VanderPlas](https://jakevdp.github.io/PythonDataScienceHandbook/05.02-introducing-scikit-learn.html#Basics-of-the-API).
- [ ] Define a function to make new predictions and explain the model coefficient.
- [ ] Organize and comment your code.

> [Do Not Copy-Paste.](https://docs.google.com/document/d/1ubOw9B3Hfip27hF2ZFnW3a3z9xAgrUDRReOEo-FHCVs/edit) You must type each of these exercises in, manually. If you copy and paste, you might as well not even do them. The point of these exercises is to train your hands, your brain, and your mind in how to read, write, and see code. If you copy-paste, you are cheating yourself out of the effectiveness of the lessons.

If your **Plotly** visualizations aren't working:
- You must have JavaScript enabled in your browser
- You probably want to use Chrome or Firefox
- You may need to turn off ad blockers
- [If you're using Jupyter Lab locally, you need to install some "extensions"](https://plot.ly/python/getting-started/#jupyterlab-support-python-35)

## Stretch Goals
- [ ] Do linear regression with two or more features.
- [ ] Read [The Discovery of Statistical Regression](https://priceonomics.com/the-discovery-of-statistical-regression/)
- [ ] Read [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf), Chapter 2.1: What Is Statistical Learning?

In [0]:
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'

# If you're working locally:
else:
    DATA_PATH = '../data/'
    
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [0]:
# Read New York City apartment rental listing data
import pandas as pd
df = pd.read_csv(DATA_PATH+'apartments/renthop-nyc.csv')
assert df.shape == (49352, 34)

In [0]:
# Remove outliers: 
# the most extreme 1% prices,
# the most extreme .1% latitudes, &
# the most extreme .1% longitudes
df = df[(df['price'] >= 1375) & (df['price'] <= 15500) & 
        (df['latitude'] >=40.57) & (df['latitude'] < 40.99) &
        (df['longitude'] >= -74.1) & (df['longitude'] <= -73.38)]

In [18]:
df.nunique()

bathrooms                  11
bedrooms                    9
created                 48149
description             37854
display_address          8675
latitude                 2266
longitude                1605
price                    2685
street_address          15136
interest_level              3
elevator                    2
cats_allowed                2
hardwood_floors             2
dogs_allowed                2
doorman                     2
dishwasher                  2
no_fee                      2
laundry_in_building         2
fitness_center              2
pre-war                     2
laundry_in_unit             2
roof_deck                   2
outdoor_space               2
dining_room                 2
high_speed_internet         2
balcony                     2
swimming_pool               2
new_construction            2
terrace                     2
exclusive                   2
loft                        2
garden_patio                2
wheelchair_access           2
common_out

In [0]:
# so reasonable varibale to use as independent variable are, bathrooms and bedrooms

In [0]:
from plotly import express as px

In [21]:
px.scatter(df, x="bedrooms", y="price", trendline="ols")

In [22]:
px.scatter(df, x="bathrooms", y="price", trendline="ols")

In [23]:
from sklearn.linear_model import LinearRegression

bedroom_model = LinearRegression()
bathroom_model = LinearRegression()

bedroom_model_x_train = df[["bedrooms"]]
bathroom_model_x_train = df[["bathrooms"]]
y_train = df["price"]

bedroom_model.fit(bedroom_model_x_train, y_train)
bathroom_model.fit(bathroom_model_x_train, y_train)

print("per increasing bedroom count of each house by 1, rent price increases by {}".format(bedroom_model.coef_[0]))
print("per increasing bathroom count of each house by 1, rent price increases by {}".format(bathroom_model.coef_[0]))


per increasing bedroom count of each house by 1, rent price increases by 853.2541675274308
per increasing bathroom count of each house by 1, rent price increases by 2573.3743950844187


In [24]:
# stuff i did for myself:
# 1. visualizing based on location

px.scatter(df, x="latitude", y="longitude", color="price")

In [25]:
#price cut based on price in 6 groups

df["price_10_percent_quantile"] = pd.cut(df["price"], 6, labels=range(0, 6)).astype("float64")
px.scatter(df, x="latitude", y="longitude", color="price_10_percent_quantile")

# df_not_chep = df[df["price_10_percent_quantile"] > 0]
# px.scatter(df_not_chep, x="latitude", y="longitude", color="price_10_percent_quantile")

In [0]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
import numpy as np

In [49]:
scaler = StandardScaler()

X = df.select_dtypes(include=np.number).copy()
Z = scaler.fit_transform(X)
pca = PCA()
pca_features = pca.fit_transform(Z)
pca.explained_variance_ratio_.shape
# pca.explained_variance_
X["PC1"] = pca_features[:, 0]

# px.scatter(df, x="latitude", y="price", color="price_10_percent_quantile")
px.scatter(X, x="PC1", y="price", trendline="ols", trendline_color_override="red")